# Visualizing Label Locations

Purpose of this notebook is to visualize the dataset tile locations on an interactive map. Run this notebook using `floodmaps-sampling` environment.

In [1]:
from pathlib import Path
import re
from netCDF4 import Dataset

In [2]:
# Absolute path to sampling folder
SAMPLING_BASE_DIR = Path("/lcrc/project/hydrosm/dma/data")
prism_file = SAMPLING_BASE_DIR / "supplementary" / "prism" / "prismprecip_20160801_20241130.nc"
texas_labels = SAMPLING_BASE_DIR / "labels" / "texas"
illinois_labels = SAMPLING_BASE_DIR / "labels" / "illinois"
other_labels = SAMPLING_BASE_DIR / "labels" / "others"
sar_coincident_labels = SAMPLING_BASE_DIR / "labels" / "sar_coincident"

### PRISM shapefile

In [3]:
# read PRISM data
with Dataset(prism_file, "r", format="NETCDF4") as nc:
    geotransform = nc["geotransform"][:]

def get_bounding_box(x, y, geotransform):
    upper_left_x, x_size, x_rotation, upper_left_y, y_rotation, y_size = geotransform
    minx = x * x_size + upper_left_x
    miny = (y + 1) * y_size + upper_left_y
    maxx = (x + 1) * x_size + upper_left_x
    maxy = y * y_size + upper_left_y

    return (minx, miny, maxx, maxy)

def get_centroid(minx, miny, maxx, maxy):
    return ((minx + maxx) / 2, (miny + maxy) / 2)

### Initialize Folium Map

In [31]:
import folium

# Use PRISM CRS EPSG 4269
m = folium.Map(location=(31.0624, -89.7708))

### Texas Dataset

In [33]:
texas_group = folium.FeatureGroup("Texas Dataset").add_to(m)
p = re.compile('label_(\d+)_(\d+)_(\d+)_(\d+).tif')
for label_path in texas_labels.glob('label_*.tif'):
    match = p.match(label_path.name)
    if match:
        y = int(match.group(3))
        x = int(match.group(4))
    else:
        raise ValueError(f'{label_path.name} does not match pattern')

    bbox = get_bounding_box(x, y, geotransform)
    minx, miny, maxx, maxy = bbox
    centroid = get_centroid(minx, miny, maxx, maxy)[::-1]

    folium.Rectangle(
        bounds=[(miny, minx), (maxy, maxx)],
        color="blue",
        weight=2,
        fill_color="lightblue",
        fill_opacity=0.5,
        fill=True
    ).add_to(texas_group)

    folium.Marker(
        location=centroid,
        icon=folium.Icon("blue"),
        popup=f"{label_path.name}").add_to(texas_group)

### Illinois Dataset

In [35]:
illinois_group = folium.FeatureGroup("Illinois Dataset").add_to(m)
p = re.compile('label_(\d+)_(\d+)_(\d+)_(\d+).tif')
for label_path in illinois_labels.glob('label_*.tif'):
    match = p.match(label_path.name)
    if match:
        y = int(match.group(3))
        x = int(match.group(4))
    else:
        raise ValueError(f'{label_path.name} does not match pattern')

    bbox = get_bounding_box(x, y, geotransform)
    minx, miny, maxx, maxy = bbox
    centroid = get_centroid(minx, miny, maxx, maxy)[::-1]

    folium.Rectangle(
        bounds=[(miny, minx), (maxy, maxx)],
        color="red",
        weight=2,
        fill_color="lightred",
        fill_opacity=0.5,
        fill=True
    ).add_to(illinois_group)

    folium.Marker(
        location=centroid,
        icon=folium.Icon("red"),
        popup=f"{label_path.name}").add_to(illinois_group)

## Others Dataset

In [39]:
others_group = folium.FeatureGroup("Others Dataset").add_to(m)
p = re.compile('label_(\d+)_(\d+)_(\d+)_(\d+).tif')
for label_path in other_labels.glob('label_*.tif'):
    match = p.match(label_path.name)
    if match:
        y = int(match.group(3))
        x = int(match.group(4))
    else:
        raise ValueError(f'{label_path.name} does not match pattern')

    bbox = get_bounding_box(x, y, geotransform)
    minx, miny, maxx, maxy = bbox
    centroid = get_centroid(minx, miny, maxx, maxy)[::-1]

    folium.Rectangle(
        bounds=[(miny, minx), (maxy, maxx)],
        color="green",
        weight=2,
        fill_color="lightgreen",
        fill_opacity=0.5,
        fill=True
    ).add_to(others_group)

    folium.Marker(
        location=centroid,
        icon=folium.Icon("green"),
        popup=f"{label_path.name}").add_to(others_group)

## SAR Coincident

In [37]:
sar_group = folium.FeatureGroup("SAR Dataset").add_to(m)
p = re.compile('label_(\d+)_(\d+)_(\d+)_(\d+).tif')
for label_path in sar_coincident_labels.glob('label_*.tif'):
    match = p.match(label_path.name)
    if match:
        y = int(match.group(3))
        x = int(match.group(4))
    else:
        raise ValueError(f'{label_path.name} does not match pattern')

    bbox = get_bounding_box(x, y, geotransform)
    minx, miny, maxx, maxy = bbox
    centroid = get_centroid(minx, miny, maxx, maxy)[::-1]

    folium.Rectangle(
        bounds=[(miny, minx), (maxy, maxx)],
        color="black",
        weight=2,
        fill_color="gray",
        fill_opacity=0.5,
        fill=True
    ).add_to(sar_group)

    folium.Marker(
        location=centroid,
        icon=folium.Icon("black"),
        popup=f"{label_path.name}").add_to(sar_group)

### Visualize in Interactive Map!

In [41]:
folium.LayerControl().add_to(m)

In [42]:
m

# SAR Dataset Locations

In [51]:
import folium

# Use PRISM CRS EPSG 4269
sar_m = folium.Map(location=(31.0624, -89.7708))

In [ ]:
sar_group = folium.FeatureGroup("SAR Dataset").add_to(sar_m)
p = re.compile(r'\d{8}_(\d+)_(\d+)')

SAR_MANUAL_PATH = Path("/lcrc/project/hydrosm/dma/data/imagery_swir/s2_s1_manual_1_5_labels")
SAR_RANDOM_PATH = Path("/lcrc/project/hydrosm/dma/data/imagery_swir/s2_s1_random_150_1_5")
all_events = list(SAR_MANUAL_PATH.glob('[0-9]*_*_*')) + list(SAR_RANDOM_PATH.glob('[0-9]*_*_*'))
tile_coordinates = set()
for event in all_events:
    # look for sar captures
    m = p.match(event.name)
    if match:
        y = int(m.group(1))
        x = int(m.group(2))
    else:
        raise ValueError(f'{event.name} does not match pattern')

    if (y, x) in tile_coordinates:
        continue
    tile_coordinates.add((y, x))

    bbox = get_bounding_box(x, y, geotransform)
    minx, miny, maxx, maxy = bbox
    centroid = get_centroid(minx, miny, maxx, maxy)[::-1]

    folium.Rectangle(
        bounds=[(miny, minx), (maxy, maxx)],
        color="black",
        weight=2,
        fill_color="gray",
        fill_opacity=0.5,
        fill=True
    ).add_to(sar_group)

    # Due to performance issues, we're not adding markers to the map

In [53]:
sar_m